# FTX reader

In [1]:
from jupyter_imports import *
from utils.io_utils import *
from histfeed.ftx_history import main

end_time= datetime.now(timezone.utc)-timedelta(days=1)#.replace(minute=0,second=0,microsecond=0)
start_time= end_time-timedelta(days=60)
halflife=timedelta(days=1)
modes=[('h','high'),('c','close'),('l','low'),('v','size')]

In [2]:
weights = pd.read_excel(os.path.join(os.sep, 'home','david',"config", "pfoptimizer",'current_weights.xlsx')).sort_values(by='optimalWeight',key=lambda f: np.abs(f),ascending=False)
coins = list(weights.set_index(['name']).drop(['USD','total']).head(5).index.map(lambda f: f.replace('-PERP','')))
weights

name         spot         mark        index    borrow  quote_borrow  \
9          USD          NaN          NaN          NaN       NaN           NaN   
7     BCH-PERP   119.725000   119.600000   119.776667  0.067047      0.026772   
8   MATIC-PERP     0.593805     0.593207     0.593991  0.067047      0.026772   
10       total          NaN          NaN          NaN       NaN           NaN   
5   1INCH-PERP     0.709000          NaN          NaN  0.040158      0.026772   
4     TRX-PERP     0.065342     0.065268     0.065363  0.080433      0.026772   
6     UNI-PERP     5.600000     5.594000     5.596623  0.011742      0.026772   
1    USDT-PERP     0.999300     0.998900     0.999220  0.026772      0.026772   
2     DOT-PERP     8.049000     8.048000     8.049758  0.040158      0.026772   
3     MKR-PERP  1010.500000  1009.500000  1009.705271  0.011742      0.026772   
0     XRP-PERP     0.371475     0.371400     0.371638  0.013386      0.026772   

    ExpectedBenchmark  funding  previousWeight  optimalWeight  ExpectedCarry  \
9            0.026772      NaN     1195.782456    2916.034436       0.000000   
7           -0.000716      NaN        0.000000    -959.206882     174.403197   
8           -0.000691      NaN      235.666745    -800.446638     151.617800   
10          -0.050430      NaN      742.669951     742.669951     349.127475   
5           -0.000341      NaN     -250.824600    -128.098220       8.073719   
4           -0.001043      NaN        0.000000    -109.541043       6.257431   
6           -0.000311      NaN        0.000000     -82.422102       5.526249   
1           -0.000189      NaN        0.000000     -50.868223       1.553407   
2           -0.000413      NaN     -781.677400     -17.143517       0.719165   
3           -0.000172      NaN        0.000000     -14.351541       0.646515   
0           -0.000365      NaN        0.000000     -11.291764       0.329997   

    RealizedCarry     excessIM     excessMM  transactionCost  spotBenchmark  \
9             0.0  2878.900939  2538.484089                0       0.026772   
7             NaN -1158.620944 -1068.758405                0            NaN   
8             NaN -1075.894451  -993.966383                0            NaN   
10            0.0   128.861821    -0.000006                0       0.026772   
5             NaN  -162.969402  -150.444242                0            NaN   
4             NaN  -139.360549  -128.649869                0            NaN   
6             NaN   -99.557224   -91.835574                0            NaN   
1             NaN   -59.933202   -55.263759                0            NaN   
2             NaN   -21.810363   -20.134108                0            NaN   
3             NaN   -18.258349   -16.855087                0            NaN   
0             NaN   -13.639263   -12.581403                0            NaN   

    FundingBenchmark                time  
9           0.000073 2022-06-24 12:00:00  
7                NaN 2022-06-24 12:00:00  
8                NaN 2022-06-24 12:00:00  
10          0.000073 2022-06-24 12:00:00  
5                NaN 2022-06-24 12:00:00  
4                NaN 2022-06-24 12:00:00  
6                NaN 2022-06-24 12:00:00  
1                NaN 2022-06-24 12:00:00  
2                NaN 2022-06-24 12:00:00  
3                NaN 2022-06-24 12:00:00  
0                NaN 2022-06-24 12:00:00

In [3]:
futures_df = main([None,'get','ftx','wide'])

INFO:histfeed.ftx_history:Logger set
INFO:histfeed.ftx_history:Cannot find the nb_of_days param. Defaulting to nb_of_days=100
INFO:histfeed.ftx_history:histfeed running with params ['get', 'ftx', 'wide']
INFO:histfeed.ftx_history:Getting history...


In [4]:
"2022-06-27 12:00:00+00:00	21308.0"
futures_df.filter(like='BTC-PERP_mark_c').index.max().replace(tzinfo=timezone.utc
                                                           )


Timestamp('2022-06-27 14:00:00+0000', tz='UTC')

### rates markets

In [5]:
selected = [df for df in futures_df.columns if any(df.split('-')[0].split('_')[0]==coin for coin in (coins+['USD']))]
prices=futures_df[[c for c in selected if any(string in c for string in ['price_c'])]]

short_rates=futures_df[[c for c in selected if any(string in c for string in ['PERP_rate_c','rate_borrow'])]]
short_rates=short_rates.ewm(halflife=halflife,times=short_rates.index).mean()

borrow_size=futures_df[[c for c in selected if any(string in c for string in ['_rate_size','price_volume'])]]

for c in coins:
    long_perp_carry=short_rates[c+'-PERP_rate_c']-short_rates['USD_rate_borrow']
    short_perp_carry=-short_rates[c+'-PERP_rate_c']-short_rates[c+'_rate_borrow']
    short_rates[c+'_best_perp_carry']= pd.concat([long_perp_carry, short_perp_carry]).max(level=0)
   # long_rates[c+'_long_future_carry']=long_rates[c+'-1231_rate_c']-short_rates['USD_rate_borrow']
   # long_rates[c+'_short_future_carry']=-long_rates[c+'-1231_rate_c']-short_rates[c+'_rate_borrow']

short_rates.filter(like='_best_perp_carry').iplot()#))

/tmp/ipykernel_230420/2503959885.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_230420/2503959885.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_230420/2503959885.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_230420/2503959885.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(leve

In [6]:
short_rates.filter(like='PERP_rate_c').iplot()#))

In [7]:
short_rates.filter(like='borrow').iplot()#))

In [8]:
pd.concat([borrow_size],axis=0).iplot()#))

### carry directionality

In [9]:
plotthat = futures_df[['BNB-PERP/rate/h',
       'BNB-PERP/rate/l', 'BNB-PERP/rate/c']]
plotthat.columns=['h','l','c']

KeyError: "None of [Index(['BNB-PERP/rate/h', 'BNB-PERP/rate/l', 'BNB-PERP/rate/c'], dtype='object')] are in the [columns]"

In [ ]:
import plotly.graph_objects as go
import numpy as np
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=plotthat.index,#+x_rev,
    y=0.5*(plotthat['l'].values+plotthat['h'].values),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line_color='rgba(255,255,255,0)',
    showlegend=False,
    name='BNB',
))
fig.add_trace(go.Scatter(
    x=plotthat.index, y=plotthat['c'].values,
    line_color='rgb(0,100,80)',
    name='Fair',
))

fig.update_traces(mode='lines')
fig.show()

In [ ]:
pd.concat([prices,short_rates.filter(like='carry')],axis=0).iplot(secondary_y=list(prices.columns))

# stopout: show min/max of premiums

In [ ]:
end_time=datetime.now(timezone.utc)#.replace(minute=0,second=0,microsecond=0)
start_time=end_time-timedelta(hours=1)
granular_df=ftx_history(dirname='',start=start_time,end=end_time,timeframe='15s',coin_list=coins)

In [ ]:
def compute_premium(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/indexes/'+modes[mode][1]).iloc[:,0]-1)*10000
def compute_premium_vs_spot(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/price/'+modes[mode][0]).iloc[:,0]-1)*10000
def compile_list(premium_list: list) -> pd.DataFrame:
    premium=premium_list[0]
    for df in premium_list[1:]:
        premium=premium.join(df,how='outer')
    return premium[~premium.index.duplicated()]

In [ ]:
granular_df['premium']=compute_premium_vs_spot(granular_df)
prices=granular_df[[c+'/price/c' for c in coins]]
granular_df[['premium']].iplot()

In [ ]:
premium=compute_premium(granular_df,mode=0)
ewMax=premium.resample('1h').max()
ewMax=ewMax[~ewMax.index.duplicated()]
pd.concat([prices,ewMax],axis=0).iplot(secondary_y=list(prices.columns))

In [ ]:
premium=compute_premium(granular_df,mode=2)
ewMin=premium.resample('1h').min()
ewMin=ewMin[~ewMin.index.duplicated()]
pd.concat([prices,ewMin],axis=0).iplot(secondary_y=list(prices.columns))